### ngram / file 가져오는 함수

In [1]:
from os import listdir
def fileids(path):
    return [path+file for file in listdir(path)]

In [2]:
def ngram(term, n=2):
    return [term[i:i+n] for i in range(len(term) - n + 1)]

### Tokenizing

In [3]:
from nltk.tokenize import word_tokenize
from konlpy.tag import Komoran

ma = Komoran()

# 여러가지 토큰 방법 일단은
def tokenize(file):
    with open(file, encoding='utf-8') as fp:
        content = fp.read()
    tokens1 = content.split() # 원시어절
    tokens2 = word_tokenize(content) # 구두점 분리 => 원시어절
    tokens3 = [_ for token in tokens2 for _ in ma.pos(token)] # 형태소-품사
    tokens4 = [token[0] for token in tokens3] # 형태소
    tokens5 = [token[0] for token in tokens3 if token[1].startswith('N')] # 명사
    tokens6 = [_ for token in tokens4 for _ in ngram(token)] # ngram

    print("..")
    print(len(tokens1))
    print(len(tokens1 + tokens2 + tokens3))
    print(len(tokens1 + tokens2 + tokens3 + tokens4 + tokens5 + tokens6))
    print(len(set(tokens1 + tokens2 + tokens3 + tokens4 + tokens5 + tokens6)))
    
    return tokens1
# token을 어떤걸 써야하나

## 구두점 및 불용어 등등 처리

In [4]:
def filecontent(file):
    with open(file, encoding='utf-8') as fp:
        content = fp.read()
    return content

In [5]:
from string import punctuation
import re

def makePattern():
    pattern = dict()

    # 구두점
    pattern1 = re.compile(r'[{0}]'.format(re.escape(punctuation)))
    pattern['punc'] = pattern1
    # corpus = pattern1.sub(' ',corpus)

    # 불용어
    pattern2 = re.compile(r'[A-Za-z0-9]{7,}')
    pattern['stop'] = pattern2
    # corpus = pattern2.sub(' ',corpus)

    # 이메일
    # pattern3 = re.compile(r'\w{2,}@\w{3,}(.\w{2,})+')
    pattern3 = re.compile(r'\w{2,}@(.?\w{2,})+')
    pattern['email'] = pattern3
    # corpus = pattern3.sub(' ',corpus)

    # 도메인
    pattern4 = re.compile(r'(.?\w{2,}){2,}')
    pattern['url'] = pattern4
    # corpus = pattern4.sub(' ',corpus)

    # 한글 이외
    pattern5 = re.compile(r'[^가-힣0-9]+')
    pattern['nonkorean'] = pattern5
    # corpus = pattern5.sub(' ',corpus)

    # WhiteSpace
    pattern6 = re.compile(r"\s{2,}")
    pattern['whitespace'] = pattern5
    # corpus = pattern6.sub(' ',corpus)
    
    return pattern

In [6]:
from collections import defaultdict

# content = filecontent(fileids('./news_crawl_project/')[-2])

pattern = makePattern()

def punc_stop(file):
    for _ in ['email', 'punc', 'stop','whitespace']:
        file = pattern[_].sub(' ',file)
    return file

def indexing(file):
    indexTerm1 = defaultdict(int)
    indexTerm2 = defaultdict(int)
    indexTerm3 = defaultdict(int)
    indexTerm4 = defaultdict(int)
    indexTerm5 = defaultdict(int)
    indexTerm6 = defaultdict(int)

    for term in word_tokenize(file):
        indexTerm1[term] += 1 # 원시어절
    
    for _ in indexTerm1:
        for t in ma.pos(_):
            indexTerm2[t] += 1 # 원시형태소+품사
            if len(t[0]) > 1: # 음절 길이로 정규화
                indexTerm3[t[0]] += 1 # 원시형태소
            if t[1].startswith('N'):
                indexTerm4[t[0]] += 1 # 명사
            for n in ngram(t[0]): # 바이그램
                indexTerm5[n] += 1
                indexTerm6[n] += 1
    
    return indexTerm4 #일단은 명사만 

## DocTermMatrix -> TermDocMatrix

In [7]:
def DTM_conversion():
    documentList = defaultdict(lambda: defaultdict(int))
    idx = 0
    for file in fileids('./news_crawl_project/'):
        documentList[idx] = indexing(punc_stop(filecontent(file)))
        idx += 1
        if idx % 100 == 0:
            print(idx, '진행중')
    return documentList
DTM = DTM_conversion()

100 진행중
200 진행중
300 진행중
400 진행중
500 진행중
600 진행중
700 진행중
800 진행중
900 진행중
1000 진행중
1100 진행중
1200 진행중


In [8]:
def TDM_conversion(DTM):
    TDM = defaultdict(lambda:defaultdict(int))
    for idx, termList in DTM.items():
        for term, freq in termList.items():
            TDM[term][idx] = freq
    return TDM
TDM = TDM_conversion(DTM)

## TermDocMatrix -> TermWeightMatrix

In [9]:
from math import sqrt, log2

N = len(DTM)

TWM = defaultdict(lambda:defaultdict(float))
DVL = defaultdict(float)

for idx, termList in DTM.items():
    if len(termList) > 0:
        maxTF = max(termList.values()) 
        
        for term, freq in termList.items():
            TF = freq/maxTF
            IDF = log2(N/len(TDM[term]))
            TWM[term][idx] = TF*IDF
            DVL[idx] += TWM[term][idx]**2
        
for idx, length in DVL.items():
    DVL[idx] = sqrt(length)

In [10]:
TWM

defaultdict(<function __main__.<lambda>()>,
            {'개': defaultdict(float,
                         {0: 0.18873141112316294,
                          2: 0.39633596335864224,
                          3: 0.49541995419830276,
                          4: 1.981679816793211,
                          5: 0.5661942333694888,
                          13: 1.1323884667389776,
                          15: 0.3302799694655352,
                          24: 0.9908399083966055,
                          25: 1.4862598625949084,
                          26: 0.5661942333694888,
                          28: 0.36030542123512926,
                          31: 0.22018664631035678,
                          35: 0.0825699923663838,
                          37: 0.39633596335864224,
                          42: 0.6605599389310703,
                          44: 0.2830971166847444,
                          46: 0.3302799694655352,
                          53: 1.1890078900759267,
                   

## Query에서 색인어 추출

In [11]:
from nltk.tokenize import sent_tokenize

def TQM_conversion(query):
    
    indexTerm1 = defaultdict(int)
    indexTerm2 = defaultdict(int)
    indexTerm3 = defaultdict(int)
    indexTerm4 = defaultdict(int)
    indexTerm5 = defaultdict(int)
    indexTerm6 = defaultdict(int)

    for _ in word_tokenize(query):
        for t in ma.pos(_):
            indexTerm2[t] += 1 # 원시형태소+품사
            if len(t[0]) > 1: # 음절 길이로 정규화
                indexTerm3[t[0]] += 1 # 원시형태소
            if t[1].startswith('N'):
                indexTerm4[t[0]] += 1 # 명사
            for n in ngram(t[0]): # 바이그램
                indexTerm5[n] += 1
                indexTerm6[n] += 1
    return indexTerm4

query = '서울시에 거래되는 아파트의 전세값은?'
TQM = TQM_conversion(query)

In [12]:
TQM

defaultdict(int, {'서울시': 1, '거래': 1, '아파트': 1, '전세': 1, '값': 1})

## 쿼리 가중치 계산

In [13]:
def QWM_conversion(TQM):
    QWM = defaultdict(float)
    alpha = 0.5
    maxTF = max(TQM.values())
    for term, ferq in TQM.items():
        TF = alpha + (1-alpha)*(freq/maxTF)
        DF = len(TWM[term]) if len(TWM[term]) > 0 else 1
        IDF = log2(N/DF)
        QWM[term] = TF*IDF
    return QWM
QWM = QWM_conversion(TQM)

In [14]:
QWM

defaultdict(float,
            {'서울시': 4.646162657157894,
             '거래': 4.042091333489033,
             '아파트': 4.080565481303669,
             '전세': 5.897701424153858,
             '값': 5.335822536545743})

## 유사도 계산 (Euclidean vs. Cosine) -> 검색결과 출력

#### Cosine

In [15]:
candidateList = defaultdict(float)
for term, weight1 in QWM.items():
    for doc, weight2 in TWM[term].items():
        innerProduct = weight1 * weight2
        candidateList[doc] += innerProduct
        
for doc, sim in candidateList.items():
    candidateList[doc] = sim/DVL[doc]
    
K = 5

for doc, sim in sorted(candidateList.items(), key=lambda x:x[1], reverse=True)[:K]:
    print('문서이름:{0} / 유사도:{1:.4f}'.format(doc, sim))
    print(punc_stop(filecontent(fileids('./news_crawl_project/')[doc])))

문서이름:270 / 유사도:1.7061
 기존 매물도 많은데 얼마 깎아야 팔리나 걱정 촛불집회까지 강남은 신도시와 무관 무덤덤 호가 올라 추격 매수는 주춤 서울 연합뉴스 서미숙 홍국기 기자 3기 신도시 발표후 집을 사겠다는 사람은 종적을 감추고 매물을 얼마나 더 싸게 내놔야 팔리겠냐는 집주인들 문의만 옵니다 수천만원 정도는 우습게 빠질 것 같네요 지난 11일 일산서구 후곡마을에 위치한 한 중개업소 대표 말이다 그는 이 곳은 지난해 9 13대책 이후 거래가 끊겨서 나온지 몇 달 된 물건들도 수두룩한데 3기 신도시 소식을 듣고 누가 집을 사겠느냐 며 지난해 5억원 하던 전용 84 아파트값이 최근 4억2천만 4억3천만원으로 내려왔지만 실거래가 되려면 이보다 더 낮춰야 할 것 이라고 말했다 지난 7일 3기 신도시 발표 이후 일산 파주 인천 서구 등 신도시의 직접적인 영향권에 있는 지역은 마치 찬물을 끼얹은 듯 시장 분위기가 냉랭했다 당장 급매물이 추가로 쏟아지거나 가격이 급락하진 않았지만 매수세가 끊기면서 집값 하락을 걱정하는 목소리가 많다 반면 강남을 비롯한 서울은 평온한 분위기 속에 최근 급매물 소진 이후 이어졌던 추격 매수세는 다소 주춤해진 모습이다 연합뉴스 자료사진 가뜩이나 안좋은데 찬물 끼얹은 수도권 외곽 이번 고양 창릉 등 3기 신도시 건설 계획에 가장 크게 반대하고 있는 일산서구 아파트 시장은 아예 매수세가 실종됐다 일산서구 주엽동의 한 중개업소 대표는 고양 원흥 삼송지구 등 인근 새 아파트 입주로 이 일대가 대규모 베드타운이 됐는데 또다시 일산신도시 절반 수준의 신도시가 들어선다고 하니 누가 집을 사겠느냐 며 신도시 발표 후 매수 문의는 한 통도 없고 기존에 매물을 내놨던 집주인들한테 얼마를 더 낮춰야 집이 팔리겠냐고 걱정하는 전화만 온다 고 분위기를 전했다 인터넷 커뮤니티 등에는 일부 사정이 다급한 매도자들이 1천만 2천만원 이상 가격을 추가로 낮춰 내놨다는 글이 올라오기도 했다 일산서구 일산동의 한 중개업소 사장은 이 곳이 2017년 8 2대책에서 

### Euclidean - 결과가 좋지않다. cosine을 쓰도록 하자

In [16]:
candidateList = defaultdict(float)
for term, docList in TWM.items():
    for doc, weight1 in docList.items():
        weight2 = QWM[term]
        candidateList[doc] += (weight1 - weight2)**2 
        
for doc, sim in candidateList.items():
    candidateList[doc] = sqrt(sim)

# for doc in DTM:
#     print(doc, len(punc_stop(filecontent(fileids('./news_crawl_project/')[doc])).split()), len(DTM[doc]), sum(DTM[doc].values()))

K = 5
for doc, sim in sorted(candidateList.items(), key=lambda x:x[1])[:K]:
    print('문서이름:{0} / 거리:{1:.4f}'.format(doc, sim))
    print(punc_stop(filecontent(fileids('./news_crawl_project/')[doc])))
    print()

문서이름:115 / 거리:4.0010
 국내에서 유튜브를 가장 많이 보는 연령대는 50대 이상 인 것으로 나타났다 50대 이상 유튜브의 사용시간은 1년 사이 두 배로 늘었다 앱 분석업체 와이즈앱이 지난 4월 전국 안드로이드 스마트폰 사용자 3만3000명을 조사한 결과 이 같이 나타났다고 14일 밝혔다 50대 이상의 유튜브 사용시간은 101억분으로 가장 많았다 이는 지난해 4월 51억분에서 두 배가량 늘어난 수치다 다음으로 10대 89억분 20대 81억분 30대 61억분 40대 57억분 등 순이었다 1인 평균 시청 시간은 10대가 평균 1895분 월 31시간 35분 으로 가장 길었다 20대 1625분 가 그 뒤를 이었고 50대 이상은 145분으로 30대 988분 와 40대 781분 보다 높았다 유튜브 앱 사용시간은 총 388억분으로 지난해 4월 258억분보다 50 늘었다 카카오톡 사용시간은 225억분 네이버 153억분 페이스북 42억분 등 순이었다 이들 앱의 사용시간은 지난해보다 각각 19 21 5 성장했지만 유튜브와의 격차는 더욱 벌어졌다 곽희양 기자 오늘의 인기뉴스 김민아 칼럼 황교안적 인 너무도 황교안적 인이낙연 총선 등판 기정사실화하나박해미 음주 사고 황민과 결국 이혼 25년 결혼생활 종지부미중 관세확전에 세계증시 패닉 공포지수 30 급등 단독 경찰의 청와대 보고용 2016년 총선 보고서 본 유명 선거 컨설턴트 우린 억만금 줘도 이런 건 못 만든다 최신 뉴스 두고 두고 읽는 뉴스 인기 무료만화 경향신문 무단전재 및 재배포 금지 1 8 1 8 

문서이름:113 / 거리:4.1545
 총 이용시간 258억 분에서 388억 분 50 키뉴스 이길주 기자 앱 리테일 분석서비스 와이즈앱이 지난 4월 한국 안드로이드 스마트폰 사용자의 세대별 사용 현황을 발표했다 전 세대를 합쳐 한국인이 가장 오래 사용한 앱은 유튜브로 4월 한달 총 사용시간 388억 분을 이용했다 그 뒤를 카카오톡 225억 분 네이버 153억 분 페이스북 42억 분의 순이었다 한국인이 오래 사용하는

# 뉴스분류 - KNN

In [17]:
query = """
[뉴스데스크] ◀ 앵커 ▶

대학교 여자 기숙사에 침입해서 여대생의 입을 틀어 막고 성폭행하려던 남자 대학생에게 법원이 집행유예를 선고했습니다.

범행 당시 술에 취해 기억을 못하는 '심신 미약 상태'가 인정된다는 건데 과연 술에 만취했다는 게 감형해줄 이유가 되는 건지, 또다시 논란이 예상됩니다.

김유나 기자입니다.

◀ 리포트 ▶

작년말 새벽 1시 반쯤, 부산대 여자 기숙사에 이 학교에 다니는 26살 남학생이 침입했습니다.

남학생은 계단에서 마주친 여학생의 입을 막은 뒤 성폭행을 시도했고, 저항하는 여학생을 마구 때려 여학생의 이가 부러지기도 했습니다.

검찰은 "초범이지만 죄질이 나쁘다"며 징역 10년을 구형했습니다.

하지만, 부산지방법원은 오늘 이 남학생에게 징역 3년에 집행유예 4년을 선고하고 법정에서 풀어줬습니다.

감경 사유는 '심신미약'.

재판부는 남학생이 술에 취해 기억이 끊긴 이른바 '블랙아웃' 상태에서 우발적으로 범행했다며 심신미약을 인정했습니다.

또 피해자와 합의했고, 사회적 유대관계가 분명하다는 점 등도 고려했다고 밝혔습니다.

법조계 일각에선 이례적인 판결이라는 반응이 나옵니다.

[정유진/변호사] "법정형이 10년 이상이거든요. 피고인에게 집행유예를 선처하기 위해서 심신미약 감경을 이례적으로 인정한 판결 같습니다."

부산 성폭력상담소 등 시민단체들도 성명을 내고, 이해할 수 없는 판결이라고 반발했습니다.

네티즌들은 판사의 딸이 이런 일을 당했어도 만취 심신미약을 이유로 풀어줬겠느냐며, 잠재적 성범죄자들에게 용기를 주는 판결이라고 비난했습니다."""

TQM = TQM_conversion(query)
QWM = QWM_conversion(TQM)

candidateList = defaultdict(float)

for term, weight1 in QWM.items():
    for doc, weight2 in TWM[term].items():
        innerProduct = weight1 * weight2
        candidateList[doc] += innerProduct
        
for doc, sim in candidateList.items():
    candidateList[doc] = sim/DVL[doc]
    
K = 7

categoryDict = defaultdict(int)
for doc, sim in sorted(candidateList.items(), key=lambda x:x[1], reverse=True)[:K]:
    category = fileids('./news_crawl_project/')[doc].split('/')[2][:2] # 카테고리
    categoryDict[category] += 1


In [18]:
result = max(categoryDict.items(), key=lambda x:x[1])
print("해당 문서는 '" + result[0] + "'분야로 분류 되었습니다. ", result[1], "/" , K, '확률입니다.')

해당 문서는 '사회'분야로 분류 되었습니다.  7 / 7 확률입니다.


# 뉴스분류 - Naive Bayes

In [19]:
from itertools import chain
from collections import defaultdict

In [20]:
import os

# 정치 / 경제 / 사회 / 생활 / IT / 국제
정치 = defaultdict(int)
정치c = 0
경제 = defaultdict(int)
경제c = 0
사회 = defaultdict(int)
사회c = 0
생활 = defaultdict(int)
생활c = 0
IT = defaultdict(int)
ITc = 0
국제 = defaultdict(int)
국제c = 0

for _ in fileids('./news_crawl_project/'):
    category = _.split('/')[2][:2]
    if category == "정치":
        정치c += 1
    elif category == "경제":
        경제c += 1
    elif category == "사회":
        사회c += 1
    elif category == "생활":
        생활c += 1
    elif category == "IT":
        ITc += 1
    elif category == "국제":
        국제c += 1
  

In [21]:
V = list(set(_ for idx in DTM.keys() for _ in DTM[idx]))
N = len(DTM)

In [22]:
for i in range(1, 10):
    for k, v in chain(정치.items(), DTM[i].items()):
        정치[k] += v

In [ ]:
정치

In [24]:
idx = 0
for _ in fileids('./news_crawl_project/'):
    category = _.split('/')[2][:2]
    if category == "정치":
        for k, v in chain(정치.items(), DTM[idx].items()):
#             print(v)
            정치[k] += v

    elif category == "경제":
        for k, v in chain(경제.items(), DTM[idx].items()):
            경제[k] += v
    elif category == "사회":
        
        for k, v in chain(사회.items(), DTM[idx].items()):
            사회[k] += v
    elif category == "생활":
        for k, v in chain(생활.items(), DTM[idx].items()):
            생활[k] += v
    elif category == "IT":
        
        for k, v in chain(IT.items(), DTM[idx].items()):
            IT[k] += v
    elif category == "국제":
        
        for k, v in chain(국제.items(), DTM[idx].items()):
            국제[k] += v
정치pc = 정치c/N
경제pc = 경제c/N
사회pc = 사회c/N
생활pc = 생활c/N
ITpc = ITc/N
국제pc = 국제c/N

In [ ]:
정치

In [ ]:
condProbC = defaultdict(float)
_condProbC = defaultdict(float)

정치countSum = sum(정치.values())
경제countSum = sum(경제.values())
사회countSum = sum(사회.values())
생활countSum = sum(생활.values())
ITcountSum = sum(IT.values())
국제countSum = sum(Tct.values())


for term, freq in Tct.items():
    condProbC[term] = (freq+1)/(countSum + len(V))

for term, freq in _Tct.items():
    _condProbC[term] = (freq+1)/(_countSum + len(V))

In [26]:
N

1252

In [27]:

# DTM[0]

In [28]:
trainingData =[
    (1, "Chinese Beijing Chinese", True),
    (2, "Chinese Chinese Shanhai", True),
    (3, "Chinese Macao", True),
    (4, "Tokyo Japan Chinese", False)
]

testingData = """
정의용·서호·박지원 통일각에서 받아
[서울신문]
DJ 서거 다음날 조문단 파견과 대조 
고착상태 남북 관계 그대로 반영 평가 
“北, 남측에 전할 메시지 정리 안된 듯”

김여정 제1부부장, 조화 전달 - 김정은 북한 국무위원장의 동생 김여정 노동당 선전선동부 제1부부장(오른쪽)이 12일 오후 이희호 여사 서거와 관련, 판문점 통일각에서 정의용 청와대 국가안보실장(가운데), 박지원 김대중평화센터 부이사장에게 김 위원장이 보내는 조화를 전달하고 있다. 2019.6.12 [통일부 제공] 연합뉴스
김정은 북한 국무위원장의 동생 김여정 노동당 선전선동부 제1부부장이 이희호 여사 별세와 관련해 12일 조화와 조전을 남측에 전달했다.

통일부는 이날 “북측이 통지문을 통해 김 위원장이 보내는 조의문과 조화를 이날 오후 5시 판문점 통일각에서 전달했다”며 “남측에서는 정의용 국가안보실장과 서호 통일부 차관, 장례위원회를 대표해 김대중평화센터 부이사장인 박지원 민주평화당 의원이 전달받았다”고 밝혔다.

앞서 2009년 8월 18일 김대중 전 대통령이 서거했을 당시 북한은 바로 다음날인 19일 김정일 국방위원장 명의의 조전을 보낸 뒤 통지문을 보내 조문단 파견 의사를 전달했다. 하지만 이번에는 판문점 북측 지역에서 조의문과 조화를 전달하며 남북 관계가 고착된 현 상황을 그대로 반영했다는 평가다.

당시 북한은 김 전 대통령 서거 사흘 뒤인 21일 김양건 노동당 통일전선부장 겸 조선아시아태평양평화위원회 위원장, 김기남 노동당 중앙위원회 비서 등 6명으로 이뤄진 조문단을 파견했다. 이들은 고려항공 특별기편으로 김포공항에 도착하자마자 김 전 대통령의 빈소에 조문했다.

김여정 제1부부장, 조전 전달 - 김정은 북한 국무위원장의 동생 김여정 노동당 선전선동부 제1부부장(오른쪽)이 12일 오후 이희호 여사 서거와 관련, 판문점 통일각에서 정의용 청와대 국가안보실장(왼쪽), 서호 통일부 차관, 박지원 김대중평화센터 부이사장에게 김 위원장이 보내는 조전을 전달하고 있다. 2019.6.12 [통일부 제공]
조문단은 당시 2박 3일간 일정으로 머물면서 ‘대남 특사’의 역할을 수행했다. 이들은 빈소에 들른 뒤 김형오 국회의장을 예방하고 김대중평화센터가 주최한 만찬에 참석했다. 다음날에는 정세균 당시 민주당 대표와 만나고 현인택 통일부 장관과 면담했다. 또 마지막 날 이명박 전 대통령과의 면담도 전격적으로 성사돼 30분간 면담을 진행했다.

이희호 여사는 2011년 12월 김정일 국방위원장 사망 당시 북한으로 직접 건너가 김 위원장을 직접 만나 애도의 뜻을 표한 바 있다.

이번에도 북한이 조문단을 파견한다면 지난 2월 하노이 북미 정상회담 결렬 이후에 지속된 소강상태를 ‘조의 정치’를 통해 돌파구를 마련할 수 있다는 점에서 북측 조문단 파견 여부가 관심사로 떠올랐지만, 북측은 조문단 파견 대신 조화와 조전을 보내 애도를 표명하는 방법을 선택했다. 여기에는 아직 입장 정리가 되지 않은 북측이 메시지를 갖고 나오기에는 시기적으로 이른감이 있다는 분석이 나온다.

이우영 북한대학교대학원 교수는 “하노이 회담 결렬 이후 하반기에 승부를 걸고 있는 북한이 아직 내부에서 남측에 전할 메시지 정리가 안 돼 있는 상황인 것 같다”며 “메시지를 논의해야 할 문재인 대통령도 북유럽 순방에 나서 한국에 없다는 시기적인 문제도 복합적으로 작용했을 것”이라고 분석했다.

임을출 경남대 극동문제연구소 교수는 “남북 모두 무게감 있는 인사들이 한자리에서 만난 만큼 비핵화 협상 과정에서 남북 공조 부분에 대한 논의가 제한적으로라도 이뤄졌을 수 있다”고 했다.

다만 김 위원장의 동생인 김 제1부부장이 직접 조화와 조의문을 전달한 것은 남북관계 개선에 노력해온 이 여사에 대한 예우를 갖춘 것으로 해석된다.

박지원 의원은 페이스북에 “북한 정부에서 우리 정부의 책임 있는 인사에게 조의문과 조화를 전달하겠다고 한 것은 하노이 북미 정상회담 이후 김 위원장이 도널드 트럼프 미국 대통령에게 보낸 친서와 함께 의미 있는 변화”라며 “이 여사의 서거와 기도가 남북 정부 간 고위급 대화로 남북 정상회담, 북미 정상회담의 물꼬가 트이는 계기를 만들어 줬다”고 했다.
"""

## Precesion(정확율) : 검색결과는 최대한 많이,
## Recall(재현율) : 유사도는 최대한 높이